# Chapter 7 - Unsupervised Learning - PCA

In [1]:
import sys
sys.path.append("../")
from utils import *

## Principal Component Analysis - Simulated Data

In [2]:
np.random.seed(1)
from scipy.stats import ortho_group
from sklearn.decomposition import PCA

R, m = ortho_group.rvs(3), 1000
# Sample data on Euclidean norm unit ball and then rotate in random direction
X = np.random.normal(size=(2, m))
X = np.c_[(X/ np.linalg.norm(X, axis=0)).T, np.random.normal(0, .1, m)]
X = X @ R

print("Data Matrix: (First 5 Samples)")
print(X[:5])

print("\nMean Vector:")
mu = X.mean(axis=0)
X_centered = X-X.mean(axis=0)
print(mu)

print("\n Sample Covariance Matrix:")
print(np.cov(X_centered.T))

print("\n Eigenvalues:")
vals, B = np.linalg.eig(np.cov(X_centered.T))
print(vals)

print("\n Eigenvectors: (column-wise)")
print(B)

print("\n Embedding of Centered Data: (First 5 Samples)")
print(X_centered[:5] @ B)

print("\n Projection Onto PCA Subspace: (First 5 Samples)")
print(X_centered[:5] @ B @ B.T + mu)

Data Matrix: (First 5 Samples)
[[ 0.96221916 -0.2453103   0.12333316]
 [-0.9142411   0.40528129  0.01196235]
 [ 0.13443196  0.67175134  0.73019925]
 [-0.45524641  0.79143359  0.4154129 ]
 [ 0.65231303  0.31737867  0.69577388]]

Mean Vector:
[0.02089578 0.01402443 0.01868874]

 Sample Covariance Matrix:
[[ 0.44930732 -0.09918228  0.08991116]
 [-0.09918228  0.31031796  0.22840585]
 [ 0.08991116  0.22840585  0.24982829]]

 Eigenvalues:
[0.00942455 0.48196758 0.51806145]

 Eigenvectors: (column-wise)
[[ 0.28966264  0.84999042 -0.44001346]
 [ 0.63744961  0.17160848  0.75113815]
 [-0.71397027  0.49806307  0.49211749]]

 Embedding of Centered Data: (First 5 Samples)
[[ 0.03264039  0.80773134 -0.55749382]
 [-0.01666525 -0.73106456  0.7020506 ]
 [-0.0558424   0.56375329  0.79423311]
 [ 0.0743893  -0.07371264  0.98868555]
 [-0.10714762  0.92598788  0.2832343 ]]

 Projection Onto PCA Subspace: (First 5 Samples)
[[ 0.96221916 -0.2453103   0.12333316]
 [-0.9142411   0.40528129  0.01196235]
 [ 0.134

In [3]:
# Transform data using PCA
pca = PCA(n_components=2).fit(X)
embedding = pca.transform(X)
projection = pca.inverse_transform(pca.transform(X))


print("\n Embedding of Centered Data: (First 5 Samples)")
print(embedding[:5])

print("\n Projection Onto PCA Subspace: (First 5 Samples)")
print(projection[:5])


 Embedding of Centered Data: (First 5 Samples)
[[ 0.55749382 -0.80773134]
 [-0.7020506   0.73106456]
 [-0.79423311 -0.56375329]
 [-0.98868555  0.07371264]
 [-0.2832343  -0.92598788]]

 Projection Onto PCA Subspace: (First 5 Samples)
[[ 9.52764461e-01 -2.66116905e-01  1.46637432e-01]
 [-9.09413802e-01  4.15904543e-01  6.38595549e-05]
 [ 1.50607413e-01  7.07348058e-01  6.90329439e-01]
 [-4.76794212e-01  7.44014154e-01  4.68524651e-01]
 [ 6.83349696e-01  3.85679884e-01  6.19273660e-01]]


In [4]:
fig = make_subplots(rows=1, cols=3, subplot_titles=[r"$\text{Original Data}$", 
                                                    r"$\text{Projection Onto Subspace}$", r"$\text{2D Embedding}$"], 
                    specs=[[{'type': 'scatter3d'}, {'type': 'scatter3d'}, {'type': 'scatter'}]], row_heights=[200])

fig.add_traces(data = [
        go.Scatter3d(x=X[:,0], y=X[:, 1], z=X[:,2], mode="markers", showlegend=False,
                     marker=dict(color="black", size=3, symbol="circle-open")),
        go.Scatter3d(x=projection[:,0], y=projection[:, 1], z=projection[:,2], mode="markers", showlegend=False,
                     marker=dict(color="black", size=3, symbol="circle-open")),
        go.Scatter(x=embedding[:,0], y=embedding[:, 1], mode="markers", showlegend=False,
                   marker=dict(color="black", size=3, symbol="circle-open"))],
    rows=[1,1,1], cols=[1,2,3])

fig.update_layout(height=300, width=1000, scene_aspectmode="cube", 
                  scene=dict(camera = dict(eye=dict(x=1.5, y=1.5, z=.3))),
                  scene2=dict(camera = dict(eye=dict(x=1.5, y=1.5, z=.3))))

fig.write_image("../figures/pca_circ.png")
fig.show()

## Principal Components Analysis - Real Data
The following consists of PCA low dimension embedding and restoring of two datasets: MNIST digits and Faces. Uncomment the loading commands of the desired dataset and run the following blocks.

In [5]:
import gzip
from scipy.stats import norm
from sklearn.preprocessing import MinMaxScaler
from sklearn.decomposition import PCA

# Load MNIST digists dataset
x_file, y_file = gzip.GzipFile('../datasets/mnist_np.npy.gz', "r"), gzip.GzipFile('../datasets/mnist_labels.npy.gz', "r")
X, y = np.load(x_file)[:10000,], np.load(y_file)[:10000]
pt_size, title = 1, "Digit"

# Uncomment to load the faces dataset
# X, y = np.load('../datasets/faces.npy').reshape((-1, 50, 50)), np.load('../datasets/faces_labels.npy')
# pt_size, title = 3, "Person"

As both datasets represent images let us visualize some samples from the datasets:

In [6]:
fig = px.imshow(X[[1,10,50,100,150]], facet_col=0, binary_string=True, height=200).\
        update_xaxes(showticklabels=False).\
        update_yaxes(showticklabels=False)

for i, label in enumerate(y[[1,10,50,100,150]]):
    fig.layout.annotations[i]['text'] = rf"$\text{{{title} {label}}}$"
    fig.layout.annotations[i]['font'] = dict(size=14)

fig.write_image(f"../pca_data_{title}.png")
fig.show()

### Low Dimantional Embedding
In order to embed the data-points (the different images) in some low dimensional space we will first represent each image as a vector instead of a matrix. Then we will usng PCA to project them onto a 2- and 3 dimensional subspaces. Notice that as PCA selects the PCs in such a way that they represent directions in space with decreasing variance, computing 3 PCs and using only the first 2 is equivalent for computing 2 PCs.

In [7]:
embeddedX = PCA(n_components=3).fit_transform(X.reshape((X.shape[0], -1)))

fig = make_subplots(rows=1, cols=2, subplot_titles=["2D Embedding", "3D Embedding"], 
                    specs=[[{'type': 'scatter'}, {'type': 'scatter3d'}]])

fig.add_traces([
    go.Scatter(x=embeddedX[:,0], y=embeddedX[:, 1], mode="markers", showlegend=False, 
               marker = dict(color=y, colorscale="Portland", size=pt_size), hovertemplate=f"{title} %{{marker.color}}<extra></extra>"),
    go.Scatter3d(x=embeddedX[:,0], y=embeddedX[:,1], z=embeddedX[:,2], mode="markers", showlegend=False,
                 marker=dict(color=y, colorscale="Portland", size=pt_size), hovertemplate=f"{title} %{{marker.color}}<extra></extra>")],
    rows=[1,1], cols=[1,2])

fig.update_layout(scene_aspectmode="cube", 
                  scene=dict(camera = dict(eye=dict(x=.1, y=2, z=0))))
fig.write_image(f"../pca_embedding_{title}.png")
fig.show()

### Visualize Principal Components
As these datasets represent images it is valuable to plot the PCs themselves and see what signal is captured by each

In [8]:
pcs = PCA(n_components=5).fit(X.reshape((X.shape[0], -1))).components_.reshape((-1, X.shape[1], X.shape[2]))

fig = px.imshow(pcs, facet_col=0, binary_string=True, height=200).\
        update_xaxes(showticklabels=False).\
        update_yaxes(showticklabels=False)

for i in range(len(pcs)):
    fig.layout.annotations[i]["text"] = rf"$\text{{PC {i+1}}}$"
    fig.layout.annotations[i]['font'] = dict(size=14)

fig.write_image(f"../pca_pcs_{title}.png")
fig.show()

### Reconstruct Images

In [ ]:
pca = PCA(n_components=100).fit(X.reshape((X.shape[0], -1)))
pcs = pca.components_.reshape((-1, X.shape[1], X.shape[2]))

img, loadings = X[150], pca.transform(X[150].reshape(1, -1)).T

reconstructed, distortion, images, scatters, titles = np.zeros_like(X[0]), [], [], [], []
for i in range(len(pca.components_)):
    # Reconstruct image using the first i principal components
    reconstructed += loadings[i] * pca.components_[i].reshape(img.shape)
    distortion.append(np.sum((img - reconstructed) ** 2))    

    # Append animation frame every other reconstruction
    if i % 2 == 0 or i == pca.n_components_-1:
        images.append([img.copy(), reconstructed.copy(), (img - reconstructed).copy()])
        scatters.append(go.Scatter(x=list(range(1, len(distortion)+1)), y=distortion, name=3, xaxis="x4", yaxis="y4", marker_color="black"))
        titles.append(rf"$\text{{ Image Reconstruction - Number of PCs: {i+1} }}$")


        
# Create figure on the basis of the animated facetted imshow figure
fig = px.imshow(np.array(images), facet_col=1, animation_frame=0, binary_string=True).\
        update_xaxes(showticklabels=False).\
        update_yaxes(showticklabels=False)

for i, (scatter, t) in enumerate(zip(*[scatters, titles])):
    fig["frames"][i]["data"] += (scatter, )
    for j in range(3):
        fig["frames"][i]["data"][j]["xaxis"]="x" if j == 0 else f"x{j+1}"
        fig["frames"][i]["data"][j]["yaxis"]="y" if j == 0 else f"y{j+1}"
    fig["frames"][i]["traces"] = [0,1,2,3]
    fig["frames"][i]["layout"]["title"] = t 
fig.add_traces(data=fig["frames"][0]["data"][-1])

# Create "template" figure to transfer layout onto the `fig` figure
layout = make_subplots(rows=2, cols=3, 
                       subplot_titles=[r"$\text{Original Image}$", r"$\text{Reconstructed Image}$", 
                                       r"$\text{Remaining Reconstruction}$", r"$\text{Reconstructuin Error}$"],
                       specs=[[{"type":"Image"}, {"type":"Image"}, {"type":"Image"}], [{"type":"xy","colspan": 3}, None, None]], row_heights=[500, 200],)

layout.update_layout(title=titles[0],
                     xaxis4=dict(range=[0, 50], autorange=False),
                     yaxis4=dict(range=[0, max(distortion)*1.2], autorange=False),
                     margin = dict(t = 100), width=800,
                     updatemenus=[dict(type="buttons", buttons=[AnimationButtons.play(), AnimationButtons.pause()])])

fig["layout"] = layout["layout"]
fig.show()

# Save Animation as animated gif
animation_to_gif(fig, f"../pca_reconstruction_{title}.gif", 1000)